In [1]:
import xarray as xr
from netCDF4 import Dataset
import pydap as dap
import numpy as np
import sklearn.cluster as cl
from eofs.xarray import Eof
import pandas as pd
import matplotlib.pyplot as plt
from mpl_toolkits.basemap import Basemap
from matplotlib.cm import get_cmap
import cartopy.crs as ccrs
import cartopy.feature
from PlotContourQuiver import *
from paraguayfloodspy.weather_type import XrEofCluster 
%matplotlib inline

See weather type codes at https://github.com/jdossgollin/paraguayfloodspy/blob/master/paraguayfloodspy/weather_type.py
[Package used in Doss-Gollin et al (to be submitted), coded by James Doss-Gollin and Ángel G. Muñoz]

## Make WT
Downloading latest model data (re-forecast)

In [2]:
#!rm -Rf hgt_ecmwf_ctrl.nc hgt_ecmwf_prtb.nc
#!curl -k -b '__dlauth_id=017a28e8531cac13efd89be8a7612c4c0754a83606f8f90270d14d84f62c28d7ff7fe8fbfb04c0495ddf938392d0bf3d9617e8b7' 'https://iridl.ldeo.columbia.edu/SOURCES/.ECMWF/.S2S/.ECMF/.reforecast/.control/.pressure_level_gh/.gh/P/500/VALUE/P/removeGRID/S/(last)/VALUE/S/removeGRID/hdate/(1997)/(2016)/RANGE/X/(-150)/(-50)/RANGE/Y/(20)/(80)/RANGE/data.nc' >hgt_ecmwf_ctrl.nc
#!curl -k -b '__dlauth_id=017a28e8531cac13efd89be8a7612c4c0754a83606f8f90270d14d84f62c28d7ff7fe8fbfb04c0495ddf938392d0bf3d9617e8b7' 'https://iridl.ldeo.columbia.edu/SOURCES/.ECMWF/.S2S/.ECMF/.reforecast/.perturbed/.pressure_level_gh/.gh/P/500/VALUE/P/removeGRID/S/(last)/VALUE/hdate/(1997)/(2016)/RANGE/X/(-150)/(-50)/RANGE/Y/(20)/(80)/RANGE/S/removeGRID/data.nc' >hgt_ecmwf_prtb.nc

In [3]:
hgt = xr.open_dataset('./hgt_ecmwf_prtb.nc',decode_times=False)
hgt=hgt.stack(time=('hdate', 'L')).T   #trick to deal with the time coordinates
hgt=hgt-np.mean(hgt,0)  #anomalies
#hgt

In [4]:
#print(hgt['time'])

For reproducibility, random seed is fixed (123):

In [5]:
wtseq = xr.DataArray(np.zeros((hgt.dims['M'],hgt.dims['time'])), dims=['member','time'])
CI = np.zeros((hgt.dims['M']),dtype=float)

for im in range(0,hgt.dims['M']):
    np.random.seed(123)
    print('--Member', im+1)
    best_centroid, best_ts, classifiability = XrEofCluster(
        hgt.isel(M=im),
        n_clusters=4,
        prop=0.8, # What proportion of variance should be retained?
        nsim=100, # How many random initializations to compute?
        pcscaling=0, # If 0: PCs are unscaled. If 1: all are rescaled
        variable='gh', # the variable name of hgt
        verbose = True # get useful info from the algorithm
    )
    wtseq[im,:]=np.int_(best_ts) # make it an integer
    CI[im]=classifiability

--Member 1
xarray-based classifiability for 4 clusters
Performing EOF decomposition of data for dimension reduction...
Number of EOFs retained is 10
Carrying out 100 k-means simulations...
Computing classifiability index for each pair of simulations...
--Member 2
xarray-based classifiability for 4 clusters
Performing EOF decomposition of data for dimension reduction...
Number of EOFs retained is 9
Carrying out 100 k-means simulations...
Computing classifiability index for each pair of simulations...
--Member 3
xarray-based classifiability for 4 clusters
Performing EOF decomposition of data for dimension reduction...
Number of EOFs retained is 10
Carrying out 100 k-means simulations...
Computing classifiability index for each pair of simulations...
--Member 4
xarray-based classifiability for 4 clusters
Performing EOF decomposition of data for dimension reduction...
Number of EOFs retained is 10
Carrying out 100 k-means simulations...
Computing classifiability index for each pair of simu

In [6]:
print(min(CI), np.mean(CI), max(CI))

0.6526530766 0.744559668819 0.870995450812


## Plot WTs

I think this code is helpful because it automates some of the tedious parts of plotting with subplots https://github.com/jdossgollin/paraguayfloodspy/blob/master/paraguayfloodspy/visualize.py

In [7]:
import paraguayfloodspy.visualize as viz

When we loop through we'll use this function to grab all data from a particular weather type

In [8]:
def selector(ds, im, wt):
    # get the days of the particular weather type
    idx = np.where(wtseq[im,:]==wt)[0]
    ds = ds.isel(time=idx)
    ds = ds.mean(dim = 'time')
    return(ds)

For example:

In [9]:
#selector(hgt['gh'].isel(M=0), im=0, wt=1)

Now set up the plot

In [10]:
wt_all = np.unique(wtseq)
n_wt = len(wt_all)
clusters = np.sort(np.unique(wtseq))

prop_days = np.zeros((hgt.dims['M'],n_wt),dtype=float)
for im in range(0,hgt.dims['M']):
    prop_days[im,] = [np.mean(wtseq[im,]==i) for i in clusters]

n_cols=hgt.dims['M']
X,Y = np.meshgrid(hgt.X, hgt.Y)

And actually plot!

In [ ]:
# Create Axes
totpan=n_cols*n_wt
fig, axes = viz.SetupAxes(ncol=n_wt, nax=totpan, proj = ccrs.PlateCarree(), figsize = [12, 15])
#fig, axes = viz.SetupAxes(ncol=n_wt, nax=totpan, proj = ccrs.Orthographic(-80, 35), figsize = [12, 15])
#fig, axes = viz.SetupAxes(ncol=n_cols, nax=n_wt, proj = ccrs.LambertConformal(-80, 35), figsize = [12, 8])

# Add the data to the plots
i=-1
#_min, _max = np.amin(hgt['gh']), np.amax(hgt['gh'])
for im in range(hgt.dims['M']):
    for wt in range(n_wt):
        i+=1
        sub = selector(hgt['gh'].isel(M=im), im=im, wt=wt+1)
        ax = viz.GetRowCol(i, axes)
        C0 = ax.contourf(X,Y, sub.values.T, transform=ccrs.PlateCarree(), vmin=-200, vmax=200, cmap='bwr')#vmin=_min, vmax=_max, cmap='bwr')
        ax.set_title('WT {}: {:.0%} of days'.format(wt+1, prop_days[im,wt]))

# Add things to the plot (can also use viz.FormatAxes)
for ax in axes.flat:
    ax.add_feature(cartopy.feature.BORDERS)
    ax.coastlines()
    ax.gridlines()

# Add Colorbar
fig.tight_layout()
fig.subplots_adjust(right=0.9)
#cax0 = fig.add_axes([0.95, 0.1, 0.03, 0.8])
cax0 = fig.add_axes([0.95, 0.45, 0.03, 0.1])   #xpos,ypos, barwidth, barheight
cbar0 = fig.colorbar(C0, cax = cax0)
cbar0.set_label('Z500 (gpm)', rotation=90)
cbar0.ax.get_yaxis().labelpad = 20
cbar0.ax.autoscale(False)

Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown


Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown


Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown


Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown


Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown


...

Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown


Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown


Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown


Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown


Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown
Unknown exception thrown


In [12]:
axes.shape

(10, 4)